<a href="https://colab.research.google.com/github/Rafi076/Authr/blob/main/FakeAV.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone https://github.com/Rafi076/FakeAV_Detection.git

Cloning into 'FakeAV_Detection'...
remote: Enumerating objects: 6, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (4/4), done.
remote: Total 6 (delta 0), reused 3 (delta 0), pack-reused 0 (from 0)
Receiving objects: 100% (6/6), done.


In [2]:
# STEP 1: Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [3]:
# STEP 2: Correct zip path (case-sensitive, and spelling checked)
zip_path = '/content/drive/MyDrive/FakeAVC_Re_Datsets/FakeAVC_reduceData.zip'
extract_to = '/content'  # Since zip already has a folder inside, extract to /content

# STEP 3: Unzip
import zipfile, os

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_to)

print("✅ Unzipped successfully!")


✅ Unzipped successfully!


In [4]:
# This should show the 4 main folders
# Show contents of the extracted folder
!ls "/content/FakeAVCeleb_v1.2"




FakeVideo-FakeAudio  meta_data.csv  RealVideo-FakeAudio
FakeVideo-RealAudio  README.txt     RealVideo-RealAudio


In [5]:
!ls /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio

 African	'Asian (South)'		'Caucasian (European)'
'Asian (East)'	'Caucasian (American)'


In [6]:
import os
import random
import torch
import torchaudio
import librosa
import cv2
import numpy as np
import matplotlib.pyplot as plt
from torchvision import transforms
from IPython.display import Audio

In [7]:


# Set root path of your extracted dataset
root_dir = '/content/FakeAVCeleb_v1.2'

# Define valid video extensions
video_extensions = ('.mp4', '.avi', '.mov', '.mkv')

# Walk through the directory and count video files
video_count = 0
for root, dirs, files in os.walk(root_dir):
    for file in files:
        if file.lower().endswith(video_extensions):
            video_count += 1

print(f"🎥 Total number of video files: {video_count}")


🎥 Total number of video files: 21544


In [8]:

# Path to only the RealVideo-RealAudio directory
rvr_audio_path = '/content/FakeAVCeleb_v1.2/RealVideo-RealAudio'

# Define valid video extensions
video_extensions = ('.mp4', '.avi', '.mov', '.mkv')

# Count videos inside RealVideo-RealAudio
video_count_rvr = 0
for root, dirs, files in os.walk(rvr_audio_path):
    for file in files:
        if file.lower().endswith(video_extensions):
            video_count_rvr += 1

print(f"🎬 Total videos in RealVideo-RealAudio: {video_count_rvr}")


🎬 Total videos in RealVideo-RealAudio: 500


In [9]:
# ✅ Install required libraries
!pip install torchaudio librosa opencv-python --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 62.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 35.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 43.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 88.8 MB/s eta 0:00:00


In [10]:
# ✅ Check if CUDA is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("🚀 Using device:", device)

🚀 Using device: cpu


In [11]:
# ✅ Set dataset root path (update this if different)
DATASET_DIR = '/content/FakeAVCeleb_v1.2'


# **Preprocessing** — Extract Frame + Generate Spectrogram
This step includes:

Extracting a mid-frame from each video (for visual input).

Extracting audio, converting to mono 16kHz, and creating a mel-spectrogram image (for audio input).

Saving both in temporary folders for use in training.

In [12]:
# STEP 2: FRAME + SPECTROGRAM EXTRACTION

import shutil
from pathlib import Path
import warnings
warnings.filterwarnings("ignore")

# ✅ Output directories for preprocessed data
PREPROCESS_DIR = '/content/preprocessed'
FRAME_DIR = os.path.join(PREPROCESS_DIR, 'frames')
SPEC_DIR = os.path.join(PREPROCESS_DIR, 'spectrograms')
os.makedirs(FRAME_DIR, exist_ok=True)
os.makedirs(SPEC_DIR, exist_ok=True)

# ✅ Video extensions to filter
video_exts = ('.mp4', '.avi', '.mov', '.mkv')

# ✅ Utility: Extract middle frame from video
def extract_middle_frame(video_path, save_path):
    cap = cv2.VideoCapture(video_path)
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    middle = frame_count // 2
    cap.set(cv2.CAP_PROP_POS_FRAMES, middle)
    ret, frame = cap.read()
    if ret:
        cv2.imwrite(save_path, frame)
    cap.release()

# ✅ Utility: Extract and save spectrogram
def extract_spectrogram(video_path, save_path):
    wav_path = '/content/temp_audio.wav'

    # Extract audio from video using ffmpeg
    os.system(f"ffmpeg -i \"{video_path}\" -vn -acodec pcm_s16le -ar 16000 -ac 1 {wav_path} -y -loglevel error")

    y, sr = librosa.load(wav_path, sr=16000)
    mel_spec = librosa.feature.melspectrogram(y=y, sr=sr, n_mels=128)
    mel_spec_db = librosa.power_to_db(mel_spec, ref=np.max)

    # Save as image
    plt.figure(figsize=(3, 3))
    librosa.display.specshow(mel_spec_db, sr=sr)
    plt.axis('off')
    plt.tight_layout()
    plt.savefig(save_path, bbox_inches='tight', pad_inches=0)
    plt.close()

    os.remove(wav_path)

# ✅ Process videos from one folder (test run on RealVideo-RealAudio only)
input_folder = os.path.join(DATASET_DIR, 'RealVideo-RealAudio')
processed = 0

for root, dirs, files in os.walk(input_folder):
    for file in files:
        if file.endswith(video_exts):
            video_path = os.path.join(root, file)
            filename = Path(video_path).stem

            # Paths to save frame and spectrogram
            frame_out = os.path.join(FRAME_DIR, f'{filename}.jpg')
            spec_out = os.path.join(SPEC_DIR, f'{filename}.png')

            try:
                extract_middle_frame(video_path, frame_out)
                extract_spectrogram(video_path, spec_out)
                processed += 1
            except Exception as e:
                print(f"Error processing {video_path}: {e}")

print(f"✅ Preprocessing complete for {processed} videos.")


✅ Preprocessing complete for 500 videos.


# **Scan All 285 Videos & Assign Labels Based on Folder Names**
Why?
We need to create a comprehensive list of all video file paths and assign labels (0 to 3) based on which category folder they belong to. This will be the foundation for train-test splitting and data loading.

In [13]:
import os
import pandas as pd

# Define label mapping based on folder names
label_map = {
    "FakeVideo-FakeAudio": 0,
    "FakeVideo-RealAudio": 1,
    "RealVideo-FakeAudio": 2,
    "RealVideo-RealAudio": 3
}

video_paths = []
labels = []

# Walk through each folder in the dataset directory
for class_folder in label_map.keys():
    folder_path = os.path.join(DATASET_DIR, class_folder)
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            if file.endswith(('.mp4', '.avi', '.mov', '.mkv')):  # Add more video extensions if needed
                full_path = os.path.join(root, file)
                video_paths.append(full_path)
                labels.append(label_map[class_folder])

# Create DataFrame
df = pd.DataFrame({
    'video_path': video_paths,
    'label': labels
})

print(f"Total videos found: {len(df)}")
print(df['label'].value_counts())

# Save the DataFrame as CSV for later use
csv_path = "/content/video_labels.csv"
df.to_csv(csv_path, index=False)
print(f"Saved video paths and labels to {csv_path}")


Total videos found: 21544
label
0    10835
1     9709
2      500
3      500
Name: count, dtype: int64
Saved video paths and labels to /content/video_labels.csv


# ** Preprocess Each Video (Frame & Spectrogram Extraction)**
🔍 Why?
To feed AVTENet, we need to extract:

Visual input → One representative frame (we’ll take the middle frame of each video)

Audio input → Convert extracted audio to a log-mel spectrogram

We’ll:

Resize frame to 128x128 (lightweight for Colab)

Create log-mel spectrogram with Librosa

Save both to temporary folders (/content/processed_data/frames/ and /content/processed_data/spectrograms/)

⚙️ **What this step will do:**
Read the saved video_labels.csv

For each video:

Extract middle frame and save as PNG

Extract audio and save log-mel spectrogram as .npy

# ** Code Block – Frame & Spectrogram Extraction**

In [14]:
import cv2
import pandas as pd
import librosa
import numpy as np
import matplotlib.pyplot as plt
import os
from moviepy.editor import VideoFileClip
from tqdm import tqdm

# Set paths to save processed data
FRAME_DIR = "/content/processed_data/frames"
SPEC_DIR = "/content/processed_data/spectrograms"
os.makedirs(FRAME_DIR, exist_ok=True)
os.makedirs(SPEC_DIR, exist_ok=True)

# Reload video list
df = pd.read_csv("/content/video_labels.csv")

def extract_middle_frame(video_path, save_path, size=(128, 128)):
    cap = cv2.VideoCapture(video_path)
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    middle = total_frames // 2
    cap.set(cv2.CAP_PROP_POS_FRAMES, middle)
    ret, frame = cap.read()
    if ret:
        frame = cv2.resize(frame, size)
        cv2.imwrite(save_path, frame)
    cap.release()

def extract_spectrogram(video_path, save_path, sr=16000, n_mels=64):
    try:
        clip = VideoFileClip(video_path)
        audio = clip.audio
        audio_array = audio.to_soundarray(fps=sr)
        if audio_array.ndim == 2:
            audio_array = np.mean(audio_array, axis=1)
        mel_spec = librosa.feature.melspectrogram(y=audio_array, sr=sr, n_mels=n_mels)
        log_mel_spec = librosa.power_to_db(mel_spec, ref=np.max)
        np.save(save_path, log_mel_spec)
        clip.close()
    except Exception as e:
        print(f"Error in spectrogram for {video_path}: {e}")

# Process all videos
for i, row in tqdm(df.iterrows(), total=len(df)):
    video_path = row['video_path']
    video_name = os.path.splitext(os.path.basename(video_path))[0]

    frame_out = os.path.join(FRAME_DIR, f"{video_name}.png")
    spec_out = os.path.join(SPEC_DIR, f"{video_name}.npy")

    extract_middle_frame(video_path, frame_out)
    extract_spectrogram(video_path, spec_out)


  0%|          | 2/21544 [00:00<1:00:41,  5.92it/s]

Error in spectrogram for /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio/Asian (East)/women/id04701/00017_id06462_Nn79kE76MA4_faceswap_id02807_wavtolip.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.
Error in spectrogram for /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio/Asian (East)/women/id04701/00017_id07799_gO6nidmxrJU_id07799_wavtolip.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.


  0%|          | 6/21544 [00:00<35:49, 10.02it/s]

Error in spectrogram for /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio/Asian (East)/women/id04701/00017_id06065_wavtolip.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.
Error in spectrogram for /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio/Asian (East)/women/id04701/00017_id06158_wavtolip.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.
Error in spectrogram for /content/FakeAVCeleb_v1.2/FakeVideo-FakeAudio/Asian (East)/women/id04701/00017_id09174_Qspzu6tyArc_id06060_wavtolip.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.


  0%|          | 10/21544 [00:00<27:34, 13.02it/s]

...

Error in spectrogram for /content/FakeAVCeleb_v1.2/RealVideo-RealAudio/Caucasian (American)/men/id01211/00023.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.


100%|█████████▉| 21542/21544 [41:40<00:00,  4.91it/s]

Error in spectrogram for /content/FakeAVCeleb_v1.2/RealVideo-RealAudio/Caucasian (American)/men/id04221/00053.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.
Error in spectrogram for /content/FakeAVCeleb_v1.2/RealVideo-RealAudio/Caucasian (American)/men/id00087/00002.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.


100%|██████████| 21544/21544 [41:40<00:00,  8.62it/s]

Error in spectrogram for /content/FakeAVCeleb_v1.2/RealVideo-RealAudio/Caucasian (American)/men/id01175/00025.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.
Error in spectrogram for /content/FakeAVCeleb_v1.2/RealVideo-RealAudio/Caucasian (American)/men/id03678/00078.mp4: arrays to stack must be passed as a "sequence" type such as list or tuple.


In [28]:
import glob

print("✅ Total frames:", len(glob.glob("/content/processed_data/frames/*.png")))
print("✅ Total specs:", len(glob.glob("/content/processed_data/spectrograms/*.npy")))


✅ Total frames: 18395
✅ Total specs: 900


In [29]:
from sklearn.model_selection import train_test_split

# Add video_name column
df = pd.read_csv("/content/video_labels.csv")
df['video_name'] = df['video_path'].apply(lambda x: os.path.splitext(os.path.basename(x))[0])

# Create mapping from disk
import glob

frame_dir = "/content/processed_data/frames"
spec_dir = "/content/processed_data/spectrograms"

frame_files = {os.path.splitext(os.path.basename(p))[0]: p for p in glob.glob(f"{frame_dir}/*.png")}
spec_files = {os.path.splitext(os.path.basename(p))[0]: p for p in glob.glob(f"{spec_dir}/*.npy")}

# Keep only valid samples
valid_names = set(frame_files) & set(spec_files) & set(df['video_name'])
df_cleaned = df[df['video_name'].isin(valid_names)].copy()

# Add full paths
df_cleaned['frame_path'] = df_cleaned['video_name'].map(frame_files)
df_cleaned['spec_path'] = df_cleaned['video_name'].map(spec_files)

# Final DataFrame for training
df_final = df_cleaned[['frame_path', 'spec_path', 'label']]
print("✅ Final cleaned samples:", len(df_final))

# Train-test split
train_df, test_df = train_test_split(df_final, test_size=0.2, stratify=df_final['label'], random_state=42)

# Save
train_df.to_csv("/content/train_split.csv", index=False)
test_df.to_csv("/content/test_split.csv", index=False)
print("✅ Saved train/test CSV files.")


✅ Final cleaned samples: 1058
✅ Saved train/test CSV files.


**Dataset Class (2-Input AVTENet)**
This dataset class will return (frame_tensor, spec_tensor, label) from your CSVs:

In [34]:
from torch.utils.data import Dataset
from PIL import Image
import torch
import numpy as np
import random

class AVTENDataset(Dataset):
    def __init__(self, dataframe, transform=None):
        self.df = dataframe.reset_index(drop=True)
        self.transform = transform

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        attempts = 0
        while attempts < 5:
            try:
                row = self.df.iloc[idx]
                frame = Image.open(row['frame_path']).convert("RGB")
                if self.transform:
                    frame = self.transform(frame)

                spec = np.load(row['spec_path'])
                spec = torch.tensor(spec, dtype=torch.float32).unsqueeze(0)
                spec = torch.nn.functional.interpolate(spec, size=(64, 64), mode='bilinear')

                label = int(row['label'])

                return frame, spec, label
            except Exception as e:
                idx = random.randint(0, len(self.df) - 1)
                attempts += 1

        # Instead of raising, return None for corrupted samples
        return None


Create Dataloaders

In [35]:
from torchvision import transforms
from torch.utils.data import DataLoader

frame_transform = transforms.Compose([
    transforms.Resize((128, 128)),
    transforms.ToTensor()
])

# Load cleaned CSVs
train_df = pd.read_csv("/content/train_split.csv")
test_df = pd.read_csv("/content/test_split.csv")

# Dataset
train_dataset = AVTENDataset(train_df, transform=frame_transform)
test_dataset = AVTENDataset(test_df, transform=frame_transform)

# ✅ Safe collate function to skip broken samples
def safe_collate(batch):
    batch = [b for b in batch if b is not None]
    if len(batch) == 0:
        return None
    return torch.utils.data.default_collate(batch)


# DataLoaders with collate_fn
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, num_workers=2, collate_fn=safe_collate)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False, num_workers=2, collate_fn=safe_collate)


print(f"✅ Train: {len(train_dataset)}, Test: {len(test_dataset)}")


✅ Train: 846, Test: 212


**Define the AVTENet Model**

This version uses MesoNet4 for frame and a 1D CNN for spectrogram:

In [36]:
import torch.nn as nn
import torch.nn.functional as F

class MesoNet4(nn.Module):
    def __init__(self):
        super(MesoNet4, self).__init__()
        self.conv1 = nn.Sequential(
            nn.Conv2d(3, 8, 3, 1, 1), nn.BatchNorm2d(8), nn.ReLU(),
            nn.MaxPool2d(2)
        )
        self.conv2 = nn.Sequential(
            nn.Conv2d(8, 8, 5, 1, 2), nn.BatchNorm2d(8), nn.ReLU(),
            nn.MaxPool2d(2)
        )
        self.conv3 = nn.Sequential(
            nn.Conv2d(8, 16, 5, 1, 2), nn.BatchNorm2d(16), nn.ReLU(),
            nn.MaxPool2d(2)
        )
        self.conv4 = nn.Sequential(
            nn.Conv2d(16, 16, 5, 1, 2), nn.BatchNorm2d(16), nn.ReLU(),
            nn.MaxPool2d(4)
        )
        self.fc = nn.Sequential(
            nn.Linear(16 * 8 * 8, 16), nn.ReLU()
        )

    def forward(self, x):
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        x = x.view(x.size(0), -1)
        x = self.fc(x)
        return x

class SpecNet(nn.Module):
    def __init__(self):
        super(SpecNet, self).__init__()
        self.net = nn.Sequential(
            nn.Conv1d(1, 16, kernel_size=3, padding=1), nn.ReLU(),
            nn.MaxPool1d(2),
            nn.Conv1d(16, 32, kernel_size=3, padding=1), nn.ReLU(),
            nn.MaxPool1d(2),
            nn.Flatten(),
            nn.Linear(32 * 16, 16), nn.ReLU()
        )

    def forward(self, x):
        # x: (B, 1, mel, time) — squeeze time dim for 1D conv
        x = F.interpolate(x, size=(64, 32))  # Force to fixed shape
        x = x.view(x.size(0), 1, -1)
        return self.net(x)

class AVTENet(nn.Module):
    def __init__(self, num_classes=4):
        super(AVTENet, self).__init__()
        self.visual = MesoNet4()
        self.audio = SpecNet()
        self.classifier = nn.Sequential(
            nn.Linear(16 + 16, 32),
            nn.ReLU(),
            nn.Linear(32, num_classes)
        )

    def forward(self, frame, spec):
        v = self.visual(frame)
        a = self.audio(spec)
        x = torch.cat([v, a], dim=1)
        return self.classifier(x)


Step 5: **Training Setup**

🔧 Loss, Optimizer, and Device Setup

In [37]:
import torch.optim as optim
import torch.nn as nn
import torch

# Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("✅ Using device:", device)

# Initialize model, loss, optimizer
model = AVTENet(num_classes=4).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)


✅ Using device: cpu


Step 6: Training Loop
**bold text**This loop:

Trains for several epochs

Reports loss every epoch

Saves best model checkpoint

In [38]:
import time

EPOCHS = 10  # Adjust as needed
best_loss = float('inf')

for epoch in range(EPOCHS):
    model.train()
    running_loss = 0.0
    total_samples = 0
    start = time.time()

    for batch in train_loader:
        if batch is None:
            # Skip batches that are None due to corrupted samples
            continue

        frames, specs, labels = batch
        frames, specs, labels = frames.to(device), specs.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = model(frames, specs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        batch_size = frames.size(0)
        running_loss += loss.item() * batch_size
        total_samples += batch_size

    if total_samples == 0:
        print("⚠️ Warning: No valid samples processed in this epoch.")
        avg_loss = float('nan')
    else:
        avg_loss = running_loss / total_samples

    print(f"📘 Epoch {epoch+1}/{EPOCHS}, Loss: {avg_loss:.4f}, Time: {time.time() - start:.2f}s")

    # Save best model
    if not torch.isnan(torch.tensor(avg_loss)) and avg_loss < best_loss:
        best_loss = avg_loss
        torch.save(model.state_dict(), "/content/avtenet_best.pth")
        print("✅ Model saved.")


⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 1/10, Loss: nan, Time: 5.79s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 2/10, Loss: nan, Time: 6.89s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 3/10, Loss: nan, Time: 7.21s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 4/10, Loss: nan, Time: 4.86s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 5/10, Loss: nan, Time: 6.72s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 6/10, Loss: nan, Time: 7.26s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 7/10, Loss: nan, Time: 4.69s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 8/10, Loss: nan, Time: 6.34s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 9/10, Loss: nan, Time: 7.15s
⚠️ Warning: No valid samples processed in this epoch.
📘 Epoch 10/10, Loss: nan, Time: 4.73s


In [27]:
import glob

frames = glob.glob("/content/processed_data/frames/*.png")
specs = glob.glob("/content/processed_data/spectrograms/*.npy")

print("Frames:", len(frames))
print("Specs:", len(specs))


Frames: 18395
Specs: 900
